# EDA — Conjunto de dados de veículos

Notebook de análise exploratória com exemplos usando plotly-express (histogramas, scatter, box, scatter matrix, etc.).

In [13]:
import pandas as pd
import plotly.express as px

# Carregar os dados (ajusta o caminho conforme a tua pasta)
df = pd.read_csv('../vehicles_us.csv')

# Diagnóstico inicial
print("--- Info Geral ---")
df.info()

print("\n--- Percentis (Detetar Outliers) ---")
print(df.describe(percentiles=[0.01, 0.05, 0.25, 0.75, 0.95, 0.99]))

print("\n--- % de Valores Nulos por Coluna ---")
print(df.isna().mean().sort_values(ascending=False))

--- Info Geral ---
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB

--- Percentis (Detetar Outliers) ---
               price    model_year     cylinders       odometer   is_4wd  \
count   51525.000000  47906.000000  46265.000000   

In [14]:
# 1. Filtro de Outliers (Limpar preços e kms irreais)
df = df.query("price.between(1000, 150000) & odometer.between(0, 450000)", engine='python')

# 2. Imputação Condicional (O toque de especialista)
# Preencher ano baseado no modelo/tipo
df['model_year'] = df.groupby(['model', 'type'])['model_year'].transform(lambda x: x.fillna(x.median()))

# Preencher quilometragem baseada no modelo/ano
df['odometer'] = df.groupby(['model', 'model_year'])['odometer'].transform(lambda x: x.fillna(x.median()))

# 3. Fallback e Formatação Final
df['model_year'] = df['model_year'].fillna(df['model_year'].median()).astype(int)
df['odometer'] = df['odometer'].fillna(df['odometer'].median())
df['paint_color'] = df['paint_color'].fillna('unknown')
df['is_4wd'] = df['is_4wd'].fillna(0).astype(bool)

print("Limpeza concluída. Valores nulos restantes:", df.isna().sum().sum())

Limpeza concluída. Valores nulos restantes: 4328


In [15]:
fig = px.scatter(
    df,
    x="odometer",
    y="price",
    color="fuel",
    facet_col="type",          # Divide o gráfico por colunas para cada tipo de carro
    hover_data=['model_year', 'model', 'condition'],
    opacity=0.6,
    title="Análise Avançada: Preço × Quilometragem por Combustível e Tipo",
    height=800
)

fig.update_layout(showlegend=True)
fig.show()

In [16]:
print("\nCorrelação Preço × Quilometragem por tipo de veículo:")
# Mostra quais categorias desvalorizam mais rápido
correlacoes = df.groupby('type')[['price', 'odometer']].corr().unstack().iloc[:,1].sort_values()
print(correlacoes)


Correlação Preço × Quilometragem por tipo de veículo:
type
bus           -0.918891
offroad       -0.690598
coupe         -0.683316
pickup        -0.609961
sedan         -0.606986
SUV           -0.606657
wagon         -0.598484
mini-van      -0.591758
convertible   -0.588117
hatchback     -0.575008
truck         -0.557017
van           -0.551278
other         -0.413058
Name: (price, odometer), dtype: float64


In [17]:
import pandas as pd
import plotly.express as px
# Carregar dados
df = pd.read_csv('../vehicles_us.csv')
# Ver nulos e estatísticas
print(df.info())
print(df.isna().sum())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB
None
price               0
model_year       3619
model               0
condition           0
cylinders        5260
fuel                0
odometer         7892
transmission        0
typ

In [18]:
# Criar coluna de marca
df['manufacturer'] = df['model'].apply(lambda x: x.split()[0])
# Limpeza inteligente: preencher nulos pela mediana do grupo
df['model_year'] = df.groupby('model')['model_year'].transform(lambda x: x.fillna(x.median()))
df['odometer'] = df.groupby('model_year')['odometer'].transform(lambda x: x.fillna(x.median()))
# Remover o que restou de nulos e outliers
df = df.dropna(subset=['model_year', 'odometer'])
df = df.query("price > 500 & odometer < 400000")
print("Dados limpos e enriquecidos!")

Dados limpos e enriquecidos!


In [19]:
# Testar o gráfico que vai para a App
fig = px.histogram(df, x="model_year", color="condition", title="Teste de Distribuição")
fig.show()